# ボルトオンのガバナンスAPI

このノートブックでは、[デプロイ済みLLMブループリント](https://docs.datarobot.com/ja/docs/gen-ai/deploy-llm.html)でボルトオンのガバナンスAPIを使用する方法がまとめられています。プレイグラウンドからデプロイされたLLMブループリントは、カスタムモデルの`custom.py`ファイルで[`chat()`フック](https://docs.datarobot.com/ja/docs/mlops/deployment/custom-models/custom-model-assembly/structured-custom-models.html#chat)をデフォルトで実装します。


## ボルトオンのガバナンスAPIを使う

[OpenAI APIの公式Pythonライブラリ](https://github.com/openai/openai-python)を使用して、DataRobot LLMブループリントデプロイにチャット補完リクエストを行うことができます。


In [ ]:
!pip install openai=="1.51.2"

In [ ]:
from openai import OpenAI

LLMブループリントのデプロイのIDとDataRobot APIトークンを指定します。


In [ ]:
DEPLOYMENT_ID = "<SPECIFY_DEPLOYMENT_ID_HERE>"
DATAROBOT_API_TOKEN = "<SPECIFY_TOKEN_HERE>"

DEPLOYMENT_URL = f"https://app.datarobot.com/api/v2/deployments/{DEPLOYMENT_ID}"

OpenAIクライアントを作成するには、以下のコードを使用します。


In [ ]:
client = OpenAI(base_url=DEPLOYMENT_URL, api_key=DATAROBOT_API_TOKEN)

チャット補完を要求するには、以下のコードを使用します。`model`パラメーター指定の詳細については、以下の [注意事項](#considerations)を参照してください。


Note that specifying the system message in the request overrides the system prompt set in the LLM blueprint. Specifying other settings in the request, such as `max_completion_tokens`, overrides the settings of the LLM blueprint. 


In [ ]:
completion = client.chat.completions.create(
    model="datarobot-deployed-llm",
    messages=[
        {"role": "system", "content": "Answer with just a number."},
        {"role": "user", "content": "What is 2+3?"},
        {"role": "assistant", "content": "5"},
        {"role": "user", "content": "Now multiply the result by 4."},
        {"role": "assistant", "content": "20"},
        {"role": "user", "content": "Now divide the result by 2."},
    ],
)

In [ ]:
print(completion)

以下のセルを使って、ストリーミングレスポンスでチャット補完を要求します。


In [ ]:
streaming_response = client.chat.completions.create(
    model="datarobot-deployed-llm",
    messages=[
        {"role": "system", "content": "Explain your thoughts using at least 100 words."},
        {"role": "user", "content": "What would it take to colonize Mars?"},
    ],
    stream=True,
)

In [ ]:
for chunk in streaming_response:
    content = chunk.choices[0].delta.content
    if content is not None:
        print(content, end="")

## 注意事項

ボルトオンのガバナンスAPIを使用する際は、以下の点に注意してください。


* 変更せずにチャット補完フックを実装した場合、`chat()`フックの動作は`score()`フックとは異なります。具体的には、変更されていない`chat()`フック [は`completion_create_params`引数](https://docs.datarobot.com/ja/docs/mlops/deployment/custom-models/custom-model-assembly/structured-custom-models.html#chat)を介して`model`パラメーターを渡しますが、`score()`フックはカスタムモデルコード内のモデルを指定します。

* [デプロイされたLLMをプレイグラウンドに追加](https://docs.datarobot.com/ja/docs/gen-ai/playground-tools/build-llm-blueprints.html#add-a-deployed-llm)すると、検証では「チャットモデルID」フィールドに入力された値が`model`パラメーターの値として使用されます。LLMのデプロイがこの値を`model`パラメーターとして受け入れることを確認します。受け入れない場合は、`chat()`フックの実装を変更して`model`パラメーターの値を上書きし、目的のモデルを定義します（ [ランタイムパラメーター](https://docs.datarobot.com/ja/docs/mlops/deployment/custom-models/custom-model-assembly/custom-model-runtime-parameters.html)を使用するなど）。詳細については、[GenAIのトラブルシューティング](https://docs.datarobot.com/ja/docs/gen-ai/genai-troubleshooting.html#custom-model-errors)を参照してください。

* ボルトオンのガバナンスAPIは、`datarobot-drum>=1.14.3`で実行されているカスタムモデルの[GPU環境](https://docs.datarobot.com/ja/docs/workbench/nxt-registry/nxt-model-workshop/nxt-open-source-textgen-template.html)でも使用できます。
